In [1]:
import os
import sys
sys.path.insert(0, '../')

import warnings
warnings.filterwarnings('ignore')

In [ ]:
# ! pip install yfinance --upgrade --no-cache-dir

In [43]:
import os
import json
import random
import numpy as np
import torch
from dataload import data_download, make_dataset
import pandas as pd 
import yfinance as yf

import json
import pickle

In [6]:
config = {
    "START" : "2001-01-01",
    "END" : "2021-12-27",
    "N_STOCK" : 50,
    "LEN_DATA" : 5000,
    "TRAIN_LEN" : 63,
    "PRED_LEN" : 21,
    "TRAIN_RATIO": 0.75
}





In [39]:
from bs4 import BeautifulSoup

# Read HTML content from file
file_path = 'data/snp500_list.html'
with open(file_path, 'r') as file:
    html_content = file.read()

# Parse the HTML content
soup = BeautifulSoup(html_content, 'html.parser')

# Find all table rows (tr)
table_rows = soup.find_all('tr')

# Initialize an empty list to store stock data
snp500_stocks = []

# Iterate through each table row to extract data
for row in table_rows:
    stock_data = {}
    columns = row.find_all('td')

    # print(row)

    # Check if the row contains data
    if len(columns) > 0:
        # print(columns)
        stock_data['No.'] = columns[0].text.strip()
        stock_data['Company'] = columns[1].text.strip()
        stock_data['Symbol'] = columns[2].text.strip()
        stock_data['Portfolio%'] = columns[3].text.strip()
        stock_data['Price'] = columns[4].text.strip()  # Extracting price
        stock_data['Chg'] = columns[5].text.strip()
        stock_data['% Chg'] = columns[6].text.strip('()')  # Removing parentheses from % Chg

        # old format 
        # No,Company,Symbol,Weight
        row_data = {}
        row_data['No'] = stock_data['No.']
        row_data['Company'] = stock_data['Company']
        row_data['Symbol'] = stock_data['Symbol']
        row_data['Weight'] = float(stock_data['Portfolio%'][:-1])
        
        # Append extracted data to the list
        snp500_stocks.append(row_data)

# Display the extracted S&P 500 stock data
for stock in snp500_stocks:
    print(stock)

# convert stock to dataframe and save to csv
df = pd.DataFrame(snp500_stocks)
df.to_csv('data/snp500_list.csv', index=False)


{'No': '1', 'Company': 'Apple Inc.', 'Symbol': 'AAPL', 'Weight': 7.32}
{'No': '2', 'Company': 'Microsoft Corp', 'Symbol': 'MSFT', 'Weight': 7.12}
{'No': '3', 'Company': 'Amazon.com Inc', 'Symbol': 'AMZN', 'Weight': 3.43}
{'No': '4', 'Company': 'Nvidia Corp', 'Symbol': 'NVDA', 'Weight': 3.01}
{'No': '5', 'Company': 'Alphabet Inc. Class A', 'Symbol': 'GOOGL', 'Weight': 2.01}
{'No': '6', 'Company': 'Meta Platforms, Inc. Class A', 'Symbol': 'META', 'Weight': 1.9}
{'No': '7', 'Company': 'Alphabet Inc. Class C', 'Symbol': 'GOOG', 'Weight': 1.73}
{'No': '8', 'Company': 'Berkshire Hathaway Class B', 'Symbol': 'BRK.B', 'Weight': 1.68}
{'No': '9', 'Company': 'Tesla, Inc.', 'Symbol': 'TSLA', 'Weight': 1.67}
{'No': '10', 'Company': 'Unitedhealth Group Incorporated', 'Symbol': 'UNH', 'Weight': 1.29}
{'No': '11', 'Company': 'Broadcom Inc.', 'Symbol': 'AVGO', 'Weight': 1.2}
{'No': '12', 'Company': 'Jpmorgan Chase & Co.', 'Symbol': 'JPM', 'Weight': 1.19}
{'No': '13', 'Company': 'Eli Lilly & Co.', 'Sym

In [41]:
snp500 = pd.read_csv("data/snp500_list.csv")
snp500.loc[snp500.Symbol == "BRK.B", "Symbol"] = "BRK-B"
snp500 = {tup[2]: tup[1] for tup in snp500.values.tolist()}
stock_pair = data_download.stock_download(
    snp500, len_data=config["LEN_DATA"], n_stock=config["N_STOCK"], download_dir='data/stocks/'
)
json.dump(stock_pair, open("data/stock.json", "w", encoding="UTF-8"))

[*********************100%%**********************]  1 of 1 completed


AAPL
[*********************100%%**********************]  1 of 1 completed
MSFT
[*********************100%%**********************]  1 of 1 completed
AMZN
[*********************100%%**********************]  1 of 1 completed
NVDA
[*********************100%%**********************]  1 of 1 completed
failed at GOOGL
[*********************100%%**********************]  1 of 1 completed
failed at META
[*********************100%%**********************]  1 of 1 completed
failed at GOOG
[*********************100%%**********************]  1 of 1 completed
BRK-B
[*********************100%%**********************]  1 of 1 completed
failed at TSLA
[*********************100%%**********************]  1 of 1 completed
UNH
[*********************100%%**********************]  1 of 1 completed
failed at AVGO
[*********************100%%**********************]  1 of 1 completed
JPM
[*********************100%%**********************]  1 of 1 completed
LLY
[*********************100%%**********************]  1 of 

In [42]:
sp500_index = yf.download("^GSPC", config["START"], config["END"])
sp500_index.to_csv("data/snp500_index.csv")

[*********************100%%**********************]  1 of 1 completed


In [45]:
path = "data/"

stock_dict_sp = json.load(open(path + "stock.json", "r", encoding="UTF8"))
return_df = make_dataset.get_return_df(stock_dict_sp)


In [46]:
return_df.head()

AAPL      MSFT      AMZN      NVDA     BRK-B       UNH  \
Date                                                                     
2002-05-24 -0.041766 -0.028869  0.001028 -0.019786  0.014229  0.005101   
2002-05-27 -0.003526 -0.008864 -0.010585 -0.020040  0.001569  0.002428   
2002-05-28 -0.003539 -0.008943 -0.010698 -0.020449  0.001566  0.002422   
2002-05-29  0.000000 -0.005173 -0.007901  0.037057 -0.018161  0.011300   
2002-05-30  0.009134  0.011271 -0.028972 -0.014716 -0.014447  0.014249   

                 JPM       LLY       XOM       JNJ  ...       DHR       TXN  \
Date                                                ...                       
2002-05-24 -0.014967 -0.016167 -0.016517 -0.005684  ...  0.007028 -0.021123   
2002-05-27 -0.007968  0.001253 -0.004859 -0.001548  ... -0.012898 -0.001502   
2002-05-28 -0.008032  0.001252 -0.004882 -0.001551  ... -0.013066 -0.001504   
2002-05-29 -0.006202  0.005145  0.011480  0.002447  ... -0.009968 -0.039582   
2002-05-30 -0.026310  0.000777 -0.023856  0.000163  ... -0.014919  0.002434   

                 UNP        BA      SPGI       HON       CAT        GE  \
Date                                                                     
2002-05-24 -0.003249 -0.018287 -0.000235 -0.029138 -0.005545 -0.010679   
2002-05-27 -0.006449 -0.004045 -0.006280 -0.003041 -0.004272 -0.008471   
2002-05-28 -0.006491 -0.004061 -0.006319 -0.003050 -0.004290 -0.008544   
2002-05-29  0.001976  0.000000  0.000792 -0.006662 -0.018682 -0.020490   
2002-05-30 -0.013083  0.015232 -0.008428  0.011696 -0.009569 -0.006390   

                 COP      AMAT  
Date                            
2002-05-24 -0.020044 -0.071734  
2002-05-27 -0.002872  0.006700  
2002-05-28 -0.002881  0.006656  
2002-05-29 -0.007324 -0.043209  
2002-05-30 -0.025975 -0.022325  

[5 rows x 50 columns]

In [52]:
def make_DL_dataset(data, data_len, n_stock):
    times = []
    dataset = np.array(data.iloc[:data_len, :]).reshape(1, -1, n_stock)
    
    time_index = data.iloc[:data_len, :].index
    print('------row------', 0)
    print(time_index)
    print(dataset.shape)
    print('\n\n')

    times.append(time_index)
    

    for i in range(1, len(data) - data_len + 1):
        addition = np.array(data.iloc[i : data_len + i, :]).reshape(1, -1, n_stock)
        dataset = np.concatenate((dataset, addition))
        time_index = data.iloc[i : data_len + i, :].index

        print('------row------', i)
        print(time_index)
        print(addition.shape)
        print(dataset.shape)
        print('\n\n')

        times.append(time_index)
    
    
    # each row is a time series of 84 days = 63 days of training + 21 days of prediction for 50 stocks
    return dataset, times


'''
  "N_STOCK" : 50,
  "LEN_DATA" : 5000,
  "TRAIN_LEN" : 63,
  "PRED_LEN" : 21,
  "TRAIN_RATIO": 0.75
'''
def data_split(data, train_len=63, pred_len=21, tr_ratio=0.75, n_stock=50):
    return_train, times_train = make_DL_dataset(
        data[: int(len(data) * tr_ratio)], train_len + pred_len, n_stock
    )
    return_test, times_test = make_DL_dataset(
        data[int(len(data) * tr_ratio) :], train_len + pred_len, n_stock
    )

    print(return_train.shape, return_test.shape)
    print(times_train[0].shape, times_test[0].shape)

    

    # each row is a time series of 84 days = 63 days of training + 21 days of prediction for 50 stocks
    x_tr = np.array([x[:train_len] for x in return_train])
    y_tr = np.array([x[-pred_len:] for x in return_train])

    # times_train is time_index of label returns only (not including feature returns)
    times_tr = np.unique(
        np.array([x[-pred_len:] for x in times_train]).flatten()
    ).tolist()

    x_te = np.array([x[:train_len] for x in return_test])
    y_te = np.array([x[-pred_len:] for x in return_test])
    times_te = np.unique(
        np.array([x[-pred_len:] for x in times_test]).flatten()
    ).tolist()

    return x_tr, y_tr, x_te, y_te, times_tr, times_te

In [53]:
'''
  "TRAIN_LEN" : 63,
  "PRED_LEN" : 21,
-->> Use three months returns to predict one month returns 

'''

x_tr, y_tr, x_te, y_te, times_tr, times_te = data_split(
    return_df,
    config["TRAIN_LEN"],
    config["PRED_LEN"],
    config["TRAIN_RATIO"],
    config["N_STOCK"],
)



------row------ 0
Index(['2002-05-24', '2002-05-27', '2002-05-28', '2002-05-29', '2002-05-30',
       '2002-05-31', '2002-06-03', '2002-06-04', '2002-06-05', '2002-06-06',
       '2002-06-07', '2002-06-10', '2002-06-11', '2002-06-12', '2002-06-13',
       '2002-06-14', '2002-06-17', '2002-06-18', '2002-06-19', '2002-06-20',
       '2002-06-21', '2002-06-24', '2002-06-25', '2002-06-26', '2002-06-27',
       '2002-06-28', '2002-07-01', '2002-07-02', '2002-07-03', '2002-07-04',
       '2002-07-05', '2002-07-08', '2002-07-09', '2002-07-10', '2002-07-11',
       '2002-07-12', '2002-07-15', '2002-07-16', '2002-07-17', '2002-07-18',
       '2002-07-19', '2002-07-22', '2002-07-23', '2002-07-24', '2002-07-25',
       '2002-07-26', '2002-07-29', '2002-07-30', '2002-07-31', '2002-08-01',
       '2002-08-02', '2002-08-05', '2002-08-06', '2002-08-07', '2002-08-08',
       '2002-08-09', '2002-08-12', '2002-08-13', '2002-08-14', '2002-08-15',
       '2002-08-16', '2002-08-19', '2002-08-20', '2002-08-

In [54]:
with open(path + "date.pkl", "wb") as f:
    pickle.dump(times_te, f)

with open(path + "dataset.pkl", "wb") as f:
    pickle.dump([x_tr, y_tr, x_te, y_te], f)